**Data Preparation** <br>
In this step, all selected research papers area read as pdf documents.
The data is read in the form of text entirely as well as page-wise.
While cleaning this data, below steps are performed:
- Identified pages where references are listed and removed references section.
- Removed references that are inline with the text, mentioned in brackets such as (author name et al, year of publication)
- Removed title of the paper from the text
- Removed email addresses, weblinks etc.

## Requirements

Please review the following requirements before starting the lesson:

* To run this notebook, you need to use one of the following Databricks runtime(s): **14.3.x-cpu-ml-scala2.12 14.3.x-scala2.12**



## Setup Installation

Install required libraries.

In [0]:
%pip install --quiet PyMuPDF mlflow==2.14.3 transformers==4.44.0 "unstructured[pdf,docx]==0.14.10" llama-index==0.10.62 pydantic==2.8.2 accelerate
dbutils.library.restartPython()

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
notebook 6.5.2 requires prometheus-client, which is not installed.
nbclassic 0.5.2 requires prometheus-client, which is not installed.
jupyter-server 1.23.4 requires prometheus-client, which is not installed.
databricks-feature-engineering 0.2.1 requires pyspark<4,>=3.1.2, which is not installed.
ydata-profiling 4.2.0 requires pydantic<2,>=1.8.1, but you have pydantic 2.8.2 which is incompatible.
databricks-sdk 0.1.6 requires requests<2.29.0,>=2.28.1, but you have requests 2.32.3 which is incompatible.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
%pip install PyPDF2  

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 4.4 MB/s eta 0:00:00
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
%pip install --upgrade urllib3 transformers
%pip uninstall -y transformers
%pip install transformers
%pip install openpyxl

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
  Using cached urllib3-2.3.0-py3-none-any.whl (128 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.0/10.0 MB 55.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 69.6 MB/s eta 0:00:00
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.26.20
    Uninstalling urllib3-1.26.20:
      Successfully uninstalled urllib3-1.26.20
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.19.1
    Uninstalling tokenizers-0.19.1:
      Successfully uninstalled tokenizers-0.19.1
  Attempting uninstall: transformers
    Found existing installation: transformers 4.44.0
    Uninstalling transformers-4.44.0:
      Successfully uninstalled transformers-4.44.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency confl

In [0]:
# articles_path = f"{DA.paths.datasets}/arxiv-articles/"
# table_name = f"{DA.catalog_name}.{DA.schema_name}.pdf_raw_text"

articles_path = "/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/"
# read pdf files
df = (
        spark.read.format("binaryfile")
        .option("recursiveFileLookup", "true")
        .load(articles_path)
        )

# save list of the files to table
# df.write.mode("overwrite").saveAsTable(table_name)

display(df.head(5))

path modificationTime length content dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85215710429.pdf 2025-03-08T19:51:29Z 6992642 JVBERi0xLjUNJeLjz9MNCjM5NiAwIG9iag08PC9MaW5lYXJpemVkIDEvTCA2OTkyNjQyL08gMzk5L0UgOTA3NDkzL04gMTUvVCA2OTkyMDUwL0ggWyA1MDcgNDAyXT4+DWVuZG9iag0gICAgICAgICAgDQo0MTQgMCBvYmoNPDw= (truncated) dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85214920027.pdf 2025-03-08T19:51:29Z 6074186 JVBERi0xLjcNJYCEiIyQlJicoKSorLC0uLzAxMjM0NTY3ODk6Ozw9Pj8DQ0xNDI1IDAgb2JqDTw8IC9UIDYwNDU1MzAgL0wgNjA3NDE4NiAvTGluZWFyaXplZCAxIC9FIDI2Nzc3MiAvTyAxNDI3IC9IDVsgMjY2MCA3NDMNXSA= (truncated) dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85202175578.pdf 2025-03-08T19:51:21Z 5969388 JVBERi0xLjYKJfbk/N8KMSAwIG9iago8PAovT3BlbkFjdGlvbiAyIDAgUgovUGFnZU1vZGUgL1VzZU91dGxpbmVzCi9TYXZlU3RyZWFtcyA8PAovUSAzIDAgUgovcSA0IDAgUgo+PgovTmFtZXMgNSAwIFIKL01ldGFkYXRhIDY= (truncated) dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85200833840.pdf 2025-03-08T19:51:15Z 4163028 JVBERi0xLjcKJeLjz9MKMSAwIG9iago8PC9Db2xvclNwYWNlL0RldmljZUdyYXkvU3VidHlwZS9JbWFnZS9IZWlnaHQgNDUvRmlsdGVyL0ZsYXRlRGVjb2RlL1R5cGUvWE9iamVjdC9XaWR0aCAyMjgvTGVuZ3RoIDMyL0JpdHM= (truncated) dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85187495340.pdf 2025-03-08T19:51:09Z 3815064 JVBERi0xLjcNJYCEiIyQlJicoKSorLC0uLzAxMjM0NTY3ODk6Ozw9Pj8DQ0xMTMyIDAgb2JqDTw8IC9UIDM3OTIyNjggL0wgMzgxNTA2NCAvTGluZWFyaXplZCAxIC9FIDI3NzE0OCAvTyAxMTM0IC9IDVsgMzIwMCA3NjUNXSA= (truncated)

In [0]:
# Read paper title from excel file
excel_file = '/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/final_dataset_for_main_data_analysis_20250303.xlsx'

from openpyxl import load_workbook  
from openpyxl.utils.dataframe import dataframe_to_rows  
import pandas as pd
workbook = load_workbook(filename=excel_file)  
worksheet = workbook['Sheet1']  
data = worksheet.values  
columns = next(data)  
df_paper_details = pd.DataFrame(data, columns=columns)  

# Get only rows where 'Status? PDF Extraction' is 'Y'
df_paper_details = df_paper_details[df_paper_details['Status? PDF Extraction'] == 'Y']
len(df_paper_details)

60

In [0]:
display(df_paper_details)

/databricks/spark/python/pyspark/sql/pandas/conversion.py:413: UserWarning: createDataFrame attempted Arrow optimization because 'spark.sql.execution.arrow.pyspark.enabled' is set to true; however, failed by the reason below:
  Expected bytes, got a 'int' object
Attempting non-optimization as 'spark.sql.execution.arrow.pyspark.fallback.enabled' is set to true.
  warn(msg)


EID Text_Type Title Authors Source title Author full names Author(s) ID Year Volume Issue Art. No. Page start Page end Page count Cited by DOI Link Abstract Author Keywords Index Keywords Document Type Publication Stage Open Access Source is_relevant_flan-t5-large is_relevant_deberta-v3-large is_relevant_distilbert-base-uncased-finetuned-sst-2-english is_relevant_mixtral_7b is_relevant_llama3 is_relevant_deberta-v3-large_nikita Count TRUE Count FALSE Status? PDF Extraction 2-s2.0-85199110741 Non_Columnar Application and Sustainability of AI and Machine Learning in the Various Stages of the Value Chain in Online Fashion Retail: A Conceptual Review Pillarisetty R.; Mishra P. Sustainability in Marketing Practice: Strategies for Industry 4.0 Pillarisetty, Radhika (59226575700); Mishra, Pratika (59225926300) 59226575700; 59225926300 2024.0 null null null 131 140 9 0.0 null https://www.scopus.com/inward/record.uri?eid=2-s2.0-85199110741&partnerID=40&md5=37a26d439361417d766f0636b64efb1a Technology enablers, particularly AI-based tools and processes, have taken the online retail industry by storm. This conceptual chapter outlines the different areas in which machine learning (ML) and deep learning algorithms contribute to enhancing the value chain of online fashion retail processes in such a way that it provides a competitive advantage and increased return on investment. Starting from the product design phase, catalog creation with visual images, manufacturing or retailing, through to customer service with chatbots, and finally the last mile of logistics and delivery of the products, technology empowered by AI is improving the value chain. The contribution of AI techniques such as supervised machine learning, collaborative filtering, k-means clustering, GAN (generative adversarial network), DNNs (deep neural networks), regression models, computer vision (CV) can be directly correlated to increased personalization for customers in giving them products they desire. This directly translates to increased customer satisfaction and loyalty. The chapter brings out the marketing and managerial implications of the use of these intelligent technologies and their sustainability. Increasingly, most retailers, both big and small, are taking advantage of AI-based technologies to improve service satisfaction, sales, and reduce product returns. © 2025 by Apple Academic Press, Inc. null null Book chapter Final null Scopus true true true true true true =COUNTIF(Y2:AD2,TRUE) =COUNTIF(Y2:AD2,FALSE) Y 2-s2.0-85206256893 Columnar Impact of Gen-AI chatbots on consumer services experiences and behaviors: Focusing on the sensation of awe and usage intentions through a cybernetic lens Pathak K.; Prakash G.; Samadhiya A.; Kumar A.; Luthra S. Journal of Retailing and Consumer Services Pathak, Kanishka (57823831500); Prakash, Gyan (57698843400); Samadhiya, Ashutosh (57202603196); Kumar, Anil (57001679600); Luthra, Sunil (43361407000) 57823831500; 57698843400; 57202603196; 57001679600; 43361407000 2025.0 82 null 104120 null null null 1.0 10.1016/j.jretconser.2024.104120 https://www.scopus.com/inward/record.uri?eid=2-s2.0-85206256893&doi=10.1016%2fj.jretconser.2024.104120&partnerID=40&md5=e2784c7eaa80022fb3e9958f54570eb7 Generative AI-based chatbots have surfaced as a magical tool, revolutionizing the service industry. Equipped with superior conversational traits and the ability to attune with the conversant, chatbots have forged a coherent bond with the conversant. The untapped potential of chatbots deserves a better understanding of how consumers interact with them. This study recruits the theory of cybernetics to shed light upon the mechanism of chatbot consumer interaction. The theory helps to explain the psychological perspectives of chatbot users and answers the all-important question as to how to craft a coherent communication by enhancing the antecedents to chatbot efficiency. A mixed-method approach is used to identify factors that add to the dynamics of c

Databricks visualization. Run in Databricks to view.

## Extract pdf file name from its path string present in column 'path'


In [0]:
def ExtractEIDFromPath(path):
    pdf_name = path.split('/')[-1]
    return pdf_name.split('.pdf')[0]
df_p = df.toPandas()
df_p['EID'] = df_p['path'].apply(lambda x: ExtractEIDFromPath(x))
# df_p.head(3)
#Join df_p with df_paper_details on EID
df_p_joined = df_p.merge(df_paper_details, on='EID', how='inner')
print(len(df_p_joined))
df_p_joined.head(3)

60


path  ... Status? PDF Extraction
0  dbfs:/Volumes/cmidev/default/preventech/data/u...  ...                      Y
1  dbfs:/Volumes/cmidev/default/preventech/data/u...  ...                      Y
2  dbfs:/Volumes/cmidev/default/preventech/data/u...  ...                      Y

[3 rows x 37 columns]

In [0]:
# Function to clean up the extracted text (optional)
import re
def clean_extracted_text(text):
    #Remove newline character 
    text = re.sub(r'\n', '', text)
    # Replace occurrences of a space followed by a period with just a period in the given text string
    return re.sub(r' ?\.', '.', text)


def pprint(obj):
  import pprint
  pprint.pprint(obj, compact=True, indent=1, width=100)

## Read non-columnar text type research papers using PyMuPDF library

In [0]:
import fitz  # PyMuPDF

# Function to extract text from PDF using PyMuPDF
def extract_doc_text(pdf_content):
    doc = fitz.open(stream=pdf_content, filetype="pdf")
    text = ""
    pages=[]
    for page in doc:
        text += page.get_text()
        pages.append(page.get_text())

    return text, pages

In [0]:
file_path = '/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles'#/2-s2.0-85215710429.pdf'
file = file_path+'/2-s2.0-85205122773.pdf'#/2-s2.0-85161398837.pdf'
# with open(f"{file.replace('dbfs:','/dbfs/')}", mode="rb") as pdf:
with open(file, mode="rb") as pdf:

  doc,pages = extract_doc_text(pdf.read()) 
  print(doc)

Citation: Gu, C.; Jia, S.; Lai, J.; Chen,
R.; Chang, X. Exploring Consumer
Acceptance of AI-Generated
Advertisements: From the
Perspectives of Perceived Eeriness
and Perceived Intelligence. J. Theor.
Appl. Electron. Commer. Res. 2024, 19,
2218–2238. https://doi.org/
10.3390/jtaer19030108
Academic Editor: Hyunchul Ahn
Received: 14 July 2024
Revised: 16 August 2024
Accepted: 22 August 2024
Published: 3 September 2024
Copyright: © 2024 by the authors.
Licensee MDPI, Basel, Switzerland.
This article is an open access article
distributed under the terms and
conditions of the Creative Commons
Attribution (CC BY) license (https://
creativecommons.org/licenses/by/
4.0/).
Article
Exploring Consumer Acceptance of AI-Generated Advertisements:
From the Perspectives of Perceived Eeriness and
Perceived Intelligence
Chenyan Gu *, Shuyue Jia
, Jiaying Lai, Ruli Chen and Xinsiyu Chang
School of Management, Guangdong University of Technology, Guangzhou 510006, China;
shuyue-jia@foxmail.com (S.J.); 32200

## Read columnar text based research papers using PyPDF2 library

In [0]:
import PyPDF2  
def extract_doc_text_pypdf2(file):

    with open(file, 'rb') as pdf_file:  
        pdf_reader = PyPDF2.PdfReader(pdf_file)  
    
        text = ''  
        for page_num in range(len(pdf_reader.pages)):  
            page = pdf_reader.pages[page_num]  
            text += page.extract_text()  
    
    # print(text) 
    return text

text = extract_doc_text_pypdf2(file)

len(text),len(doc)

(89782, 84334)

**Get titles mentioned in bold text as a section header from research paper text**<br>
This function works for both columnar and non-columnar text based research papers


In [0]:
# Identify section titles
import fitz  # PyMuPDF library

def GetTitlesFromPaper(file):
    pdf_document = fitz.open(file)
    # pdf_document = PyPDF2.PdfReader(file)  

    # print("pdf_document",pdf_document)
    # Initialize a list to store section titles in bold
    bold_section_titles = []

    # Iterate through each page in the PDF
    for page_num in range(pdf_document.page_count):
        page = pdf_document[page_num]

        
        # Get the text elements with their formatting
        text_elements = page.get_text("dict")

        # Identify section titles in bold
        for element in text_elements.get("blocks", []):  # Check if "blocks" key exists
            for line in element.get("lines", []):  # Check if "lines" key exists
                for span in line.get("spans", []):  # Check if "spans" key exists
                    text = span.get("text", "")
                    font_flags = span.get("flags", 0)
                    # print(text,font_flags,font_flags & 1 << 5)
                    # Check if the font style is bold
                    # if font_flags & 1 << 5:  # Check if the bold flag is set
                    if font_flags ==20:
                        bold_section_titles.append(text)

    # Print or process the section titles in bold
    # print(bold_section_titles)
    titles = []
    for title in bold_section_titles:
        # print(title)
        titles.append(title.lower())

    #Clean up titles by stripping any leading or trailing space
    titles = [title.strip() for title in titles]
    #Remove page numbers appearing as titles if title is a number
    titles = [title for title in titles if not title.isnumeric()]
    # Close the PDF document
    pdf_document.close()
    return titles

In [0]:
titles=GetTitlesFromPaper(file)
titles

['citation:',
 'copyright:',
 'exploring consumer acceptance of ai-generated advertisements:',
 'from the perspectives of perceived eeriness and',
 'perceived intelligence',
 'chenyan gu *, shuyue jia',
 ', jiaying lai, ruli chen and xinsiyu chang',
 '*',
 'abstract:',
 'keywords:',
 '1. introduction',
 '2. literature review and hypotheses',
 'h1a:',
 'h1b:',
 'h2a:',
 'h2b:',
 'h3a:',
 'h3b:',
 'h4a:',
 'h4b:',
 'h5a:',
 'h5b:',
 'h6:',
 'h7:',
 'figure 1.',
 '3. methodology',
 '4. data analysis and results',
 'table 1.',
 'demographic',
 'frequency',
 '%',
 'table 1.',
 'demographic',
 'frequency',
 '%',
 'table 2.',
 'construct',
 'items',
 'std. loading',
 'cronbach',
 'α',
 'cr',
 'ave',
 'table 2.',
 'construct',
 'items',
 'std. loading',
 'cronbach',
 'α',
 'cr',
 'ave',
 'table 3.',
 'construct',
 'im',
 'pe',
 'pi',
 'sy',
 'vi',
 'wa',
 've',
 'table 4.',
 'construct',
 'im',
 'pe',
 'pi',
 'sy',
 'vi',
 'wa',
 've',
 'table 4.',
 'construct',
 'im',
 'pe',
 'pi',
 'sy',
 'v

## Remove footer text

In [0]:
import fitz  # PyMuPDF library  
def GetFilteredText(file):
    # Open the PDF file  
    pdf_document = fitz.open(file)  
    
    # Define footer coordinates (x0, y0, x1, y1)  
    footer_coords = (73, 796, 430, 819)  # Example coordinates  
    # footer_coords = (70.85653686523438, 764.563232421875, 94.52005004882812, 775.3682861328125)
    
    # Initialize a list to store text outside the footer coordinates  
    filtered_text = []  
    footer_text = []
    # Iterate through each page in the PDF  
    for page_num in range(pdf_document.page_count):  
        page = pdf_document[page_num]  
        
        # Get the text elements with their bounding boxes  
        text_elements = page.get_text("dict")  
        # print(text_elements)
        # Filter text elements outside the footer region  
        for element in text_elements["blocks"]:  
            if "lines" in element:
                if not any(  
                    x0 >= footer_coords[0] and y0 >= footer_coords[1] and x1 <= footer_coords[2] and y1 <= footer_coords[3]   
                    for line in element["lines"] for span in line["spans"]   
                    for x0, y0, x1, y1 in [span["bbox"]]  
                ):  
                    # print(x0,y0,x1,y1)

                    # print("filtered text:", element)
                    filtered_text.extend([span["text"] for line in element["lines"] for span in line["spans"]])  
                else:                
                    print("-----footer text:", element)
                    footer_text.extend([span["text"] for line in element["lines"] for span in line["spans"]])  

    
    # Combine the filtered text elements  
    filtered_text_combined = " ".join(filtered_text)  
    
    # Print or process the filtered text  
    # print(filtered_text_combined)  
    
    # Close the PDF document  
    pdf_document.close()
    return filtered_text_combined

In [0]:
file_format ='Non Columnar' 
if file_format== 'Columnar':
    filtered_text_combined = text
else:
    filtered_text_combined = GetFilteredText(file)
len(filtered_text_combined)

85806

## Set prompt for extracting references from text

In [0]:
parser_system_prompt = "You are a AI assistant, who will be reviewing research papers to find out the references mentioned in the paper and return that text. References may be mentioned at the end. References are generally mentioned under section 'References'. These references would a text containing names of authors followed by title of their paper and their year of publication. You need to identify all such references and return the text. Do not generate any explaination text. If no references are found in the paper, then return null."

        
parser_user_prompt = "Example1 Input= 'To advance our system, we intend to incorporate additional train- ing samples from long-tail categories and integrate user personalization data. This approach aims to en- hance the accuracy and personalization of product descriptions, thereby increasing adoption rates and aiding users in efficiently producing high-quality descriptions. References Josh Achiam, Steven Adler, Sandhini Agarwal, Lama Ahmad, Ilge Akkaya, Florencia Leoni Aleman, Diogo Almeida, Janko Altenschmidt, Sam Altman, Shyamal Anadkat, et al. 2023. Gpt-4 technical report. arXiv preprint arXiv:2303.08774 . Reza Yazdani Aminabadi, Samyam Rajbhandari, Am- mar Ahmad Awan, Cheng Li, Du Li, Elton Zheng, Olatunji Ruwase, Shaden Smith, Minjia Zhang, Jeff Rasley, et al. 2022. Deepspeed-inference: enabling efficient inference of transformer models at unprece- dented scale. In  SC22: International Conference for High Performance Computing, Networking, Storage and Analysis , pages 1–15. IEEE. A Data Processing Our model’s training data comprises tasks related to product description generation, e-commerce domain understanding, and general capability tasks. The methods for collecting and constructing data for each type of task vary accordingly'. Expected output is: 'Josh Achiam, Steven Adler, Sandhini Agarwal, Lama Ahmad, Ilge Akkaya, Florencia Leoni Aleman, Diogo Almeida, Janko Altenschmidt, Sam Altman, Shyamal Anadkat, et al. 2023. Gpt-4 technical report. arXiv preprint arXiv:2303.08774 . Reza Yazdani Aminabadi, Samyam Rajbhandari, Am- mar Ahmad Awan, Cheng Li, Du Li, Elton Zheng, Olatunji Ruwase, Shaden Smith, Minjia Zhang, Jeff Rasley, et al. 2022. Deepspeed-inference: enabling efficient inference of transformer models at unprece- dented scale. In  SC22: International Conference for High Performance Computing, Networking, Storage and Analysis , pages 1–15. IEEE' Example2 Input ='In the beginning, there was database marketing. The idea was that technology could capture important attributes about customers and their relationship with a company'. And expected output =''"

parser_user_prompt_combo = "Please examin given text and extract References mentioned in the paper for below set of input. "


## Function to extract references using prompt and an LLM model

In [0]:
from openai import OpenAI
import os
DATABRICKS_TOKEN = dbutils.notebook.entry_point.getDbutils().notebook().getContext().apiToken().get()

# print(DATABRICKS_TOKEN)
# Set the OpenAI API key as an environment variable
DATABRICKS_TOKEN = dbutils.notebook.entry_point.getDbutils().notebook().getContext().apiToken().get()

os.environ['OPENAI_API_KEY'] = DATABRICKS_TOKEN#os.environ.get('DATABRICKS_TOKEN')
def ExtractReferences(parser_text):
    client = OpenAI(
    api_key=os.environ['OPENAI_API_KEY'],
    base_url="https://adb-7018564609060221.1.azuredatabricks.net/serving-endpoints"
    )

    chat_completion = client.chat.completions.create(
    messages=[

        {"role": "system", "content": parser_system_prompt +" "+ parser_user_prompt},
        {"role": "user", "content": parser_user_prompt_combo + " " + parser_text}

    ],
    model="databricks-mixtral-8x7b-instruct",
    max_tokens=8192
    )

    options = (chat_completion.choices[0].message.content)
    
    return options                


In [0]:
# #if text is too long, provide text only after references found in titles
# import re
# if "references" in titles:
#     #find all indices of references in filtered_text_combined
#     matches = ( [match.start() for match in re.finditer('(?={})'.format(re.escape("references")), filtered_text_combined)] ) 

#     # print(filtered_text_combined.find("references"))
#     # ref_indices = [i for i, x in enumerate(filtered_text_combined) if x == "references"]
#     # print(ref_indices)
#     # truncated_text_idx = filtered_text_combined.rindex("references")
#     truncated_text = filtered_text_combined[matches[-1]:]
#     # print("truncated_text:",truncated_text)
# references = ExtractReferences(truncated_text)
# references

In [0]:
references = ExtractReferences(filtered_text_combined)
references

---------------------------------------------------------------------------
BadRequestError                           Traceback (most recent call last)
File <command-638625539738536>, line 1
----> 1 references = ExtractReferences(filtered_text_combined)
      2 references

File <command-638625539738535>, line 16, in ExtractReferences(parser_text)
     10 def ExtractReferences(parser_text):
     11     client = OpenAI(
     12     api_key=os.environ['OPENAI_API_KEY'],
     13     base_url="https://adb-7018564609060221.1.azuredatabricks.net/serving-endpoints"
     14     )
---> 16     chat_completion = client.chat.completions.create(
     17     messages=[
     18 
     19         {"role": "system", "content": parser_system_prompt +" "+ parser_user_prompt},
     20         {"role": "user", "content": parser_user_prompt_combo + " " + parser_text}
     21 
     22     ],
     23     model="databricks-mixtral-8x7b-instruct",
     24     max_tokens=8192
     25     )
     27     options = (c

**Assumption:**
It is assumed that, the research papers have either "References" mentioned under a bold titled section or references are available on a separate page. If references as a title is not found in the "titles" list, then a page is searched for this and research text is considered till that page. If any text is found after references section, then it is discarded from further analysis.

## Remove references identified by the LLM model from overall text

In [0]:
def RemoveReferences(text,titles):
    
    text = text.lower()
    text = text.replace("\u2003","")
    text = text.replace("\t","")

    # titles = titles.lower()

    #Find index where "Reference" title and find next title
    ref_index = text.rindex("references")
    print("Index of reference:",ref_index)

    if titles[-1] == "references":
        print("References section found at the end")
        #References is the last section of the paper
        #Take text before References section
        text_without_reference = text[:ref_index]
    elif "references" in titles:
        print("References section found in the middle of the paper")

        #References are added in the middle of the paper
        next_title = titles[titles.index("references")+1]
        print("next_title:",next_title)

        post_ref_text = text[ref_index:]
        next_title_location = post_ref_text.find(next_title)
        print("next title location:",next_title_location)
        #Get text before ref_index and after next_title
        text_without_reference = text[:ref_index-1]+post_ref_text[next_title_location:]
    else:
        print("References not found")

        #Paper does not have references listed, return the text as is
        text_without_reference = text
    return text_without_reference

# try:
#     # len(titles):
#     clean_text = RemoveReferences(filtered_text_combined)
# except:
#     #check if reference is on any page
#     clean_text=''
#     for p in pages:
#         if "References" in p:
#             #Found page number with references mentioned on it

#             page_num_ref = pages.index(p)
#             print("References found on page number:",page_num_ref)
#             for p in range(page_num_ref):
#                 clean_text += pages[p]
# clean_text

In [0]:
titles[-1]

'disclaimer/publisher’s note:'

In [0]:
len(filtered_text_combined),filtered_text_combined.rindex("references"),len(references)

(85806, 10462, 614)

In [0]:
clean_text = RemoveReferences(filtered_text_combined, titles)
clean_text

Index of reference: 65508
References section found in the middle of the paper
next_title: disclaimer/publisher’s note:
next title location: 19928


'citation:  gu, c.; jia, s.; lai, j.; chen, r.; chang, x. exploring consumer acceptance of ai-generated advertisements: from the perspectives of perceived eeriness and perceived intelligence.  j. theor. appl. electron. commer. res.  2024 ,  19 , 2218–2238. https://doi.org/ 10.3390/jtaer19030108 academic editor: hyunchul ahn received: 14 july 2024 revised: 16 august 2024 accepted: 22 august 2024 published: 3 september 2024 copyright:  © 2024 by the authors. licensee mdpi, basel, switzerland. this article is an open access article distributed under the terms and conditions of the creative commons attribution (cc by) license (https:// creativecommons.org/licenses/by/ 4.0/). article exploring consumer acceptance of ai-generated advertisements: from the perspectives of perceived eeriness and perceived intelligence chenyan gu *, shuyue jia , jiaying lai, ruli chen and xinsiyu chang school of management, guangdong university of technology, guangzhou 510006, china; shuyue-jia@foxmail.com (s.j.

In [0]:
if "references" in titles:
    clean_text = RemoveReferences(filtered_text_combined,titles)
else:
    #check if reference is on any page
    for p in pages:
        if "References" in p or "REFERENCES" in p:
            #Found page number with references mentioned on it

            page_num_ref = pages.index(p)
            print("References found on page number:",page_num_ref)
            for p in range(page_num_ref):
                clean_text += pages[p]
        else:
            #No refereces found
            clean_text = filtered_text_combined

Index of reference: 65508
References section found in the middle of the paper
next_title: disclaimer/publisher’s note:
next title location: 19928


In [0]:
len(clean_text)

65877

In [0]:
#Run code on research papers to get text without references
#papers path is listed in column df['path']. Read all paths and remove 'dbfs:' from path text
# df_p = df.toPandas()
papers = df_p_joined['path'].tolist()
text_types = df_p_joined['Text_Type'].tolist()
papers = [paper.replace("dbfs:","") for paper in papers]
sanitized_papers=[]
for file,text_type in zip(papers,text_types):
    print(file,text_type )
    if text_type == 'Columnar':
        filtered_text_combined = extract_doc_text_pypdf2(file)
    else:
        with open(file, mode="rb") as pdf:
            doc,pages = extract_doc_text(pdf.read()) 
        filtered_text_combined = GetFilteredText(file)


    #Get titles from the file
    titles = GetTitlesFromPaper(file)
    
    # references = ExtractReferences(filtered_text_combined)
    clean_text=''
    # if "References" in titles or "REFERENCES" in titles:
    print("Total titles found",len(titles))

    if (len(titles) > 0):
        if text_type == 'Columnar':
            clean_text = RemoveReferences(filtered_text_combined,titles)

        else:
            if "references" in titles:
                clean_text = RemoveReferences(filtered_text_combined,titles)
            else:
                #check if reference is on any page
                for p in pages:
                    if "References" in p or "REFERENCES" in p:
                        #Found page number with references mentioned on it

                        page_num_ref = pages.index(p)
                        print("References found on page number:",page_num_ref)
                        for p in range(page_num_ref):
                            clean_text += pages[p]
                    else:
                        #No refereces found
                        clean_text = filtered_text_combined
    else:
        #Titles not extracted, leave the text as is
        clean_text = filtered_text_combined

    
    sanitized_papers.append(clean_text)
df_p['Cleaned_Text_Raw']=sanitized_papers

    

/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85215710429.pdf Columnar
Total titles found 185
Index of reference: 30010
References section found in the middle of the paper
next_title: a
next title location: 16
/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85214920027.pdf Columnar
Total titles found 28
Index of reference: 41192
References section found at the end
/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85202175578.pdf Columnar
Total titles found 21
Index of reference: 23296
References not found
/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85200833840.pdf Columnar
Total titles found 0
/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85187495340.pdf Columnar
Total titles found 42
Index of reference: 76088
References section found at the end
/Volumes/cmidev/default/prev

In [0]:
#Find total length of column  Cleaned_Text and add it into a new column called Total_Leangth
df_p['Total_Length'] = df_p['Cleaned_Text_Raw'].apply(lambda x: len(x))
 

In [0]:
display(df_p.head(3))

path modificationTime length content EID Cleaned_Text_Raw Total_Length dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85215710429.pdf 2025-03-08T19:51:29Z 6992642 JVBERi0xLjUNJeLjz9MNCjM5NiAwIG9iag08PC9MaW5lYXJpemVkIDEvTCA2OTkyNjQyL08gMzk5L0UgOTA3NDkzL04gMTUvVCA2OTkyMDUwL0ggWyA1MDcgNDAyXT4+DWVuZG9iag0gICAgICAgICAgDQo0MTQgMCBvYmoNPDw= (truncated) 2-s2.0-85215710429 proceedings of the 2024 conference on empirical methods in natural language processing: industry track , pages 697–711
november 12-16, 2024 ©2024 association for computational linguistics
ipl: leveraging multimodal large language models for intelligent
product listing
kang chen*,1,2,†qingheng zhang*,1chengbao lian*,1yixin ji1xuwei liu1
shuguang han1,‡guoqiang wu1fei huang1jufeng chen1
1alibaba group2fudan university
kchen24@m.fudan.edu.cn, {qingheng.zqh, lianchengbao.lcb, jiyixin.jyx,
xuweiliu.lxw, shuguang.sh, kingwu.wgq, jufeng.cjf}@alibaba-inc.com
abstract
unlike professional business-to-consumer
(b2c) e-commerce platforms (e.g., amazon),
consumer-to-consumer (c2c) platforms (e.g.,
facebook marketplace) are mainly targeting
individual sellers who usually lack sufficient
experience in e-commerce. individual sellers
often struggle to compose proper descriptions
for selling products. with the recent advance-
ment of multimodal large language models
(mllms), we attempt to integrate such state-
of-the-art generative ai technologies into the
product listing process. to this end, we develop
ipl, an intelligent product listing tool tailored
to generate descriptions using various product
attributes such as category, brand, color, condi-
tion, etc. ipl enables users to compose prod-
uct descriptions by merely uploading photos
of the selling product. more importantly, it
can imitate the content style of our c2c plat-
form xianyu1. this is achieved by employing
domain-specific instruction tuning on mllms,
and by adopting the multi-modal retrieval-
augmented generation (rag) process. a com-
prehensive empirical evaluation demonstrates
that the underlying model of ipl significantly
outperforms the base model in domain-specific
tasks while producing less hallucination. ipl
has been successfully deployed in our produc-
tion system, where 72% of users have their pub-
lished product listings based on the generated
content, and those product listings are shown
to have a quality score 5.6% higher than those
without ai assistance.
1 introduction
with the rise of the circular economy, second-
hand e-commerce has played a vital role in our
daily lives. unlike business-to-consumer (b2c)
*these authors contributed equally to this work.
†work done during an internship at alibaba group.
‡corresponding author: shuguang han (email:
shuguang.sh@alibaba-inc.com)
1xianyu is the largest c2c e-commerce platform in
china.
figure 1: intelligent product listing on c2c platforms
e-commerce (e.g., amazon, walmart), second-
hand e-commerce is often operating in the form of
consumer-to-consumer (c2c) transactions. dif-
ferent from professional sellers on b2c platforms,
individual sellers in second-hand marketplaces are
usually inexperienced. they face unique chal-
lenges when listing their products — navigating
through the complicated listing procedure, and cre-
ating high-quality product descriptions. these is-
sues not only affect the success rate of product
listings but also impact the overall quality and dis-
coverability of the listed products.
to address the above issues, it is imperative to
simplify the listing process for individual users
by leveraging automation to generate high-quality
product descriptions. a typical product listing pro-
cess involves users manually filling in basic prod-
uct attributes, uploading product photos, and com-
posing content descriptions. among these steps,
preparing product photos is relatively straightfor-
ward. if we can automatically generate product de-
scriptions based on the uploaded photos, it would
significant

In [0]:
#Find EID where Total_Length is 0 or <1000 in df_p
df_p[df_p['Total_Length'] < 5000]

Empty DataFrame
Columns: [path, modificationTime, length, content, EID, Cleaned_Text_Raw, Total_Length]
Index: []

In [0]:
#Check what the is minimum value of the column Total_Length
df_p=df_p.sort_values('Total_Length',ascending=True)
display(df_p)

path modificationTime length content EID Cleaned_Text_Raw Total_Length dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85210022786.pdf 2025-03-08T19:51:24Z 3647289 JVBERi0xLjUKJeLjz9MKMSAwIG9iago8PC9Db2xvclNwYWNlL0RldmljZUdyYXkvU3VidHlwZS9JbWFnZS9IZWlnaHQgMTAwNC9GaWx0ZXIvRmxhdGVEZWNvZGUvVHlwZS9YT2JqZWN0L1dpZHRoIDEwMDMvTGVuZ3RoIDk5OS8= (truncated) 2-s2.0-85210022786 tutorial on landing generative ai in industrial social and
e-commerce recsys
da xu
linkedin
sunnyvale, california, usa
dxu2@linkedin.comdanqing zhang
amazon
palo alto, california, usa
danqinz@amazon.comlingling zheng
microsoft
redmond, washington, usa
linzheng@microsoft.com
bo yang
amazon
palo alto, california, usa
byyng@amazon.comguangyu yang
tiktok
santa clara, california, usa
guangyu.yang@tiktok.comshuyuan xu
tiktok
san jose, california, usa
shuyuan.xu@rutgers.edu
cindy liang
linkedin
sunnyvale, california, usa
cliang@linkedin.com
abstract
over the past two years, gai has evolved rapidly, influencing vari-
ous fields including social and e-commerce recsys. despite exciting
advances, landing these innovations in real-world recsys remains
challenging due to the sophistication of modern industrial product
and systems. our tutorial begins with a brief overview of building
industrial recsys and gai fundamentals, followed by the ongoing
efforts and opportunities to enhance personalized recommenda-
tions with foundation models.
we then explore the integration of curation capabilities into
recsys, such as repurposing raw content, incorporating external
knowledge, and generating personalized insights/explanations to
foster transparency and trust. next, the tutorial illustrates how ai
agents can transform recsys through interactive reasoning and
action loops, shifting away from traditional passive feedback mod-
els. finally, we shed insights on real-world solutions for human-ai
alignment and responsible gai practices.
a critical component of the tutorial is detailing the ai, infras-
tructure, llmops, and product roadmap (including the evaluation
and responsible ai practices) derived from the production solutions
in linkedin, amazon, tiktok, and microsoft. while gai in recsys
is still in its early stages, this tutorial provides valuable insights
and practical solutions for the recsys and gai communities.
ccs concepts
•computing methodologies →artificial intelligence; •in-
formation systems →information retrieval.
permission to make digital or hard copies of all or part of this work for personal or
classroom use is granted without fee provided that copies are not made or distributed
for profit or commercial advantage and that copies bear this notice and the full citation
on the first page. copyrights for components of this work owned by others than the
author(s) must be honored. abstracting with credit is permitted. to copy otherwise, or
republish, to post on servers or to redistribute to lists, requires prior specific permission
and/or a fee. request permissions from permissions@acm.org.
cikm ’24, october 21–25, 2024, boise, id, usa
©2024 copyright held by the owner/author(s). publication rights licensed to acm.
acm isbn 979-8-4007-0436-9/24/10
https://doi.org/10.1145/3627673.3679099keywords
information retrieval, recommender system, generative ai, indus-
trial system, large language model
acm reference format:
da xu, danqing zhang, lingling zheng, bo yang, guangyu yang, shuyuan
xu, and cindy liang. 2024. tutorial on landing generative ai in industrial
social and e-commerce recsys. in proceedings of the 33rd acm international
conference on information and knowledge management (cikm ’24), october
21–25, 2024, boise, id, usa. acm, new york, ny, usa, 5 pages. https://doi.
org/10.1145/3627673.3679099
1 target audience, prerequisites, interests and
benefits
target audience
•both novice and expert researchers and scholars studying
recsys and gai will find this tutorial valuable for understand-
ing the most recent advancements and pra

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
# Join df_p_joined and df_p on EID
df_p_joined = df_p_joined.merge(df_p, on='EID')


Entity Based Clearning of Text

In [0]:
parser_system_prompt = "You are a AI assistant, who will be reviewing research papers and need to identify the reference text inline with other text. The inline references are mentioned such as (last name of author, year of publication, etc) or (last name of author, et al., etc). You need to identify such inline references. Do not give any explaination if no inline references are found. If no inline reference is found, return '' as output. If inline references are found at multiple places in given text, return them as a list."


        
parser_user_prompt = "Example1 Input= 'including energy-saving approaches, sustainable packaging, and plausible advertisingstrategies (Gleim et al., 2023; Park et al., 2022)'. Expected output is '(Gleim et al., 2023; Park et al., 2022)'.Example2 Input= 'maintain sustainable practices in theproduction, storage, and delivery of products and services (Cherian &Jacob, 2012; Mehraj et al., 2023; Musgrove et al., 2018). This trust isgrowing among the younger generations'. Expected output is '(Cherian &Jacob, 2012; Mehraj et al., 2023; Musgrove et al., 2018)'.  "

parser_user_prompt_combo = "Please examin given text and return inline reference text from below text. "

def RemoveInlineReferences(parser_text):
    client = OpenAI(
    api_key=os.environ['OPENAI_API_KEY'],
    base_url="https://adb-7018564609060221.1.azuredatabricks.net/serving-endpoints"
    )

    chat_completion = client.chat.completions.create(
    messages=[

        {"role": "system", "content": parser_system_prompt +" "+ parser_user_prompt},
        {"role": "user", "content": parser_user_prompt_combo + " " + parser_text}

    ],
    model="databricks-mixtral-8x7b-instruct",
    max_tokens=8192
    )

    options = (chat_completion.choices[0].message.content)
    
    return options 

## Prompt to remove figure title from paper text

In [0]:
parser_system_prompt = "You are a AI assistant, who will be reviewing research papers and need to identify the figre title text inline with other text. The inline fFigure #: Title text \n. You need to identify such inline figure titles and return it. If no inline figure title is found, return '' as output. If inline figure titles are found in given text, return them as a list. Please do not provide any additional explaination in either case."


        
parser_user_prompt = "Example1 Input= 'The first part of the survey aims to offer a concise overview of existing industrial recsys and several key deficiencies, and the Figure 2: Illustration of the GAI foundations that will be the focus areas of our tutorial'. Expected output is 'Figure 2: Illustration of the GAI foundations that will be the focus areas of our tutorial'. Example1 Input= 'Figure 3: Overview of the predominant trends of using GAI to improve personalized retrieval and ranking in social and ecommerce Recsys. We also include rendering and interaction stages in the circle for completeness. \n major advancements in GAI with a specific focus on GAI production fundamentals and LLMOps (Figure 2). Expanding upon these..'. Expected output is: 'Figure 3: Overview of the predominant trends of using GAI to improve personalized retrieval and ranking in social and ecommerce Recsys. We also include rendering and interaction stages in the circle for completeness. \n'."

parser_user_prompt_combo = "Please examin given text and return figure title text from below text. "

def RemoveInlineFigureTitle(parser_text):
    client = OpenAI(
    api_key=os.environ['OPENAI_API_KEY'],
    base_url="https://adb-7018564609060221.1.azuredatabricks.net/serving-endpoints"
    )

    chat_completion = client.chat.completions.create(
    messages=[

        {"role": "system", "content": parser_system_prompt +" "+ parser_user_prompt},
        {"role": "user", "content": parser_user_prompt_combo + " " + parser_text}

    ],
    model="databricks-mixtral-8x7b-instruct",
    max_tokens=8192
    )

    options = (chat_completion.choices[0].message.content)
    
    return options 

In [0]:
import re
def RemoveEmailAddress(parser_text):
    
    email_pattern = r'[\w\.-]+@[\w\.-]+'
    #find email address from parser_text and remove it
    return re.sub(email_pattern, '', parser_text)

def RemoveWeblink(parser_text):
    website_pattern = r"(?i)\b(?:https?://)?(?:www\.)?[\w\.-]+\.\w+\b"    
    return re.sub(website_pattern, '', parser_text)

In [0]:
# clean_text = RemoveEmailAddress(sanitized_text)
# clean_text
# clean_text = RemoveWeblink(clean_text)
# clean_text
# inline_Ref = RemoveInlineReferences(clean_text)

# clean_text = clean_text.replace(inline_Ref, '')
# clean_text

## Remove title text from Cleaned_Text_Raw


In [0]:
raw_text = df_p_joined['Cleaned_Text_Raw'].tolist()
title_text = df_p_joined['Title'].tolist()
removed_title=[]
for text,title in zip(raw_text,title_text):
    removed_title.append(text.replace(title,''))
df_p_joined['Untitled_Text'] = removed_title

## Remove author names from text from Untitled_Text


In [0]:
raw_text = df_p_joined['Untitled_Text'].tolist()
title_text = df_p_joined['Authors'].tolist()
removed_author=[]
for text,title in zip(raw_text,title_text):
    authors = title.split(';')
    for author in authors:
        text = text.replace(author,'')
    removed_author.append(text)
df_p_joined['Authorless_Text'] = removed_author

In [0]:
raw_text = df_p_joined['Authorless_Text'].tolist()
cleaned_text = []
for text in raw_text:
    # print(file)
    clean_text = RemoveEmailAddress(text)
    clean_text = RemoveWeblink(clean_text)
    # clean_text = RemoveInlineReferences(clean_text)
    try:
        inline_Ref = RemoveInlineReferences(clean_text)
        print(inline_Ref)
        print("Inline References found:",inline_Ref)

        if type(inline_Ref) == list:
            for r in inline_Ref:
                clean_text = clean_text.replace(r, '')
        else:
            clean_text = clean_text.replace(inline_Ref, '')
    except:
        print("Too long token, skipping")
    
    try:
    
        inline_figure_titles = RemoveInlineFigureTitle(clean_text)
        print("Figure titles found:",inline_figure_titles)

        if type(inline_figure_titles) == list:
            for f in inline_figure_titles:
                clean_text = clean_text.replace(f, '')
        else:
            clean_text = clean_text.replace(inline_figure_titles, '')
    except:
        print("Too long token, skipping")

    #Further sanitize the text
    sanitized_text = clean_extracted_text(clean_text)
    #pretty print the text
    # pprint(sanitized_text)
    cleaned_text.append(sanitized_text)

df_p_joined['Cleaned_Text']=cleaned_text



Figure 2: Overview of the Intelligent Product Listing (ipl) System Architecture.

Figure 1: Intelligent Product Listing on C2C Platforms.

Figure 2: Online Multi-Modal Retrieval-Augmented Generation (RAG) Process for Identifying Similar Products.

Table 1: Instruction Tuning Training Data.

Table 3: Attribute Extraction Instruction Examples.

Table 4: Performance of Domain-Specific Models Trained with Different Proportions of the Dataset.

Table 5: Model Performance in Description Generation Style on C2C Domain Based on Human Evaluation.

Table 6: Performance of Different Models on Open-Source Benchmarks to Evaluate Their General Capabilities.

Table 7: Evaluation of Component Ablation Effects in Retrieval-Augmented Generation Models.

Table 8: Examples of Different Instruction Designs for Product Description Generation.

Table 9: Sample of Automatically Generated General Instructional QA Data Based on Product Photos Using Large Language Model Prompt.

Table 10: Instruction Fine-Tunin

In [0]:
#Find total length of column  Cleaned_Text and add it into a new column called Total_Leangth
df_p_joined['Total_Length'] = df_p_joined['Cleaned_Text'].apply(lambda x: len(x))

In [0]:
display(df_p_joined)

/databricks/spark/python/pyspark/sql/pandas/conversion.py:413: UserWarning: createDataFrame attempted Arrow optimization because 'spark.sql.execution.arrow.pyspark.enabled' is set to true; however, failed by the reason below:
  Expected bytes, got a 'int' object
Attempting non-optimization as 'spark.sql.execution.arrow.pyspark.fallback.enabled' is set to true.
  warn(msg)


path_x modificationTime_x length_x content_x EID Text_Type Title Authors Source title Author full names Author(s) ID Year Volume Issue Art. No. Page start Page end Page count Cited by DOI Link Abstract Author Keywords Index Keywords Document Type Publication Stage Open Access Source is_relevant_flan-t5-large is_relevant_deberta-v3-large is_relevant_distilbert-base-uncased-finetuned-sst-2-english is_relevant_mixtral_7b is_relevant_llama3 is_relevant_deberta-v3-large_nikita Count TRUE Count FALSE Status? PDF Extraction path_y modificationTime_y length_y content_y Cleaned_Text_Raw Total_Length Untitled_Text Authorless_Text Cleaned_Text dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85215710429.pdf 2025-03-08T19:51:29Z 6992642 JVBERi0xLjUNJeLjz9MNCjM5NiAwIG9iag08PC9MaW5lYXJpemVkIDEvTCA2OTkyNjQyL08gMzk5L0UgOTA3NDkzL04gMTUvVCA2OTkyMDUwL0ggWyA1MDcgNDAyXT4+DWVuZG9iag0gICAgICAgICAgDQo0MTQgMCBvYmoNPDw= (truncated) 2-s2.0-85215710429 Columnar IPL: Leveraging Multimodal Large Language Models for Intelligent Product Listing Chen K.; Zhang Q.; Lian C.; Ji Y.; Liu X.; Han S.; Wu G.; Huang F.; Chen J. EMNLP 2024 - 2024 Conference on Empirical Methods in Natural Language Processing, Proceedings of the Industry Track Chen, Kang (59419550600); Zhang, Qingheng (57258371200); Lian, Chengbao (59419540700); Ji, Yixin (59419566900); Liu, Xuwei (59419545700); Han, Shuguang (55364695500); Wu, Guoqiang (59419540800); Huang, Fei (57210150087); Chen, Jufeng (57890895900) 59419550600; 57258371200; 59419540700; 59419566900; 59419545700; 55364695500; 59419540800; 57210150087; 57890895900 2024.0 null null null 697 711 14 0.0 null https://www.scopus.com/inward/record.uri?eid=2-s2.0-85215710429&partnerID=40&md5=57acb4d3a22e36bbcc031aa711145ae4 Unlike professional Business-to-Consumer (B2C) e-commerce platforms (e.g., Amazon), Consumer-to-Consumer (C2C) platforms (e.g., Facebook marketplace) are mainly targeting individual sellers who usually lack sufficient experience in e-commerce. Individual sellers often struggle to compose proper descriptions for selling products. With the recent advancement of Multimodal Large Language Models (MLLMs), we attempt to integrate such state-of-the-art generative AI technologies into the product listing process. To this end, we develop IPL, an Intelligent Product Listing tool tailored to generate descriptions using various product attributes such as category, brand, color, condition, etc. IPL enables users to compose product descriptions by merely uploading photos of the selling product. More importantly, it can imitate the content style of our C2C platform Xianyu1. This is achieved by employing domain-specific instruction tuning on MLLMs, and by adopting the multi-modal Retrieval-Augmented Generation (RAG) process. A comprehensive empirical evaluation demonstrates that the underlying model of IPL significantly outperforms the base model in domain-specific tasks while producing less hallucination. IPL has been successfully deployed in our production system, where 72% of users have their published product listings based on the generated content, and those product listings are shown to have a quality score 5.6% higher than those without AI assistance. © 2024 Association for Computational Linguistics. null Commerce; Computational linguistics; Sales; AI Technologies; B2C e-commerce; Business to Consumer; Commerce platforms; Domain specific; E- commerces; Facebook; Language model; Multi-modal; State of the art; Marketplaces Conference paper Final null Scopus true true true true true true =COUNTIF(Y10:AD10,TRUE) =COUNTIF(Y10:AD10,FALSE) Y dbfs:/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/research_articles/2-s2.0-85215710429.pdf 2025-03-08T19:51:29Z 6992642 JVBERi0xLjUNJeLjz9MNCjM5NiAwIG9iag08PC9MaW5lYXJpemVkIDEvTCA2OTkyNjQyL08gMzk5L0UgOTA3NDkzL04gMTUvVCA2OTkyMDUwL0ggWyA1MDcgNDAyXT4+DWVuZG9iag0gICAgICAgICAgDQo0MTQgMCBvYmoNPDw= (truncated) proceedings of the 2024 confer

Databricks visualization. Run in Databricks to view.

In [0]:
# len(df_p_joined), df_p_joined['Total_Length'].min()

(60, 15384)

In [0]:
#Write df_p_joined into a excel file by selecting columns of interest

df_p_joined_select = df_p_joined[['EID','Title','Text_Type','path_x','Authors','Cleaned_Text','Total_Length','Link']]
# df_p_joined_select['Total_Length'] = df_p_joined_select['Cleaned_Text'].apply(lambda x: len(x))
# df_p_joined_select.to_excel("/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/CleanedTextResearchPapers.xlsx")


In [0]:
import pandas as pd

# Function to clean illegal characters from the dataframe
def clean_illegal_characters(df):
    illegal_characters = ['\x00', '\x01', '\x02', '\x03', '\x04', '\x05', '\x06', '\x07', '\x08', '\x09', '\x0A', '\x0B', '\x0C', '\x0D', '\x0E', '\x0F', '\x10', '\x11', '\x12', '\x13', '\x14', '\x15', '\x16', '\x17', '\x18', '\x19', '\x1A', '\x1B', '\x1C', '\x1D', '\x1E', '\x1F']
    for col in df.columns:
        df[col] = df[col].astype(str).apply(lambda x: ''.join([c if c not in illegal_characters else '' for c in x]))
    return df

# Clean the dataframe
df_p_joined_select_cleaned = clean_illegal_characters(df_p_joined_select)

# Write the cleaned dataframe to a local Excel file
local_path = '/tmp/CleanedTextResearchPapers.xlsx'
df_p_joined_select_cleaned.to_excel(local_path, index=False)

# Move the local file to the desired location using Databricks utilities
dbutils.fs.mv(f'file:{local_path}', '/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/CleanedTextResearchPapers.xlsx')

/root/.ipykernel/2760/command-509206709702028-1759860516:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[col] = df[col].astype(str).apply(lambda x: ''.join([c if c not in illegal_characters else '' for c in x]))


True

In [0]:
cleaned_text_file = '/Volumes/cmidev/default/preventech/data/user_files/gf591/ML/fads/CleanedTextResearchPapers.xlsx'
df_p_joined_select = pd.read_excel(cleaned_text)
display(df_p_joined_select)

## ******* End of Text Reading and Cleaning *********

# Preprocess and chunk text using pretrained model tokenizer

In [0]:
import io
import os
import pandas as pd 

from llama_index.core.node_parser import SentenceSplitter
from llama_index.core.schema import Document
from llama_index.core.utils import set_global_tokenizer
from transformers import AutoTokenizer
from typing import Iterator
from pyspark.sql.functions import col, udf, length, pandas_udf, explode
from unstructured.partition.auto import partition


@pandas_udf("array<string>")
def read_as_chunk(batch_iter: Iterator[pd.Series]) -> Iterator[pd.Series]:
    # set llama2 as tokenizer
    set_global_tokenizer(
      AutoTokenizer.from_pretrained("hf-internal-testing/llama-tokenizer")
    )
    # sentence splitter from llama_index to split on sentences
    splitter = SentenceSplitter(chunk_size=100, chunk_overlap=20)
    def extract_and_split(txt):
      # txt = extract_doc_text(b)
      nodes = splitter.get_nodes_from_documents([Document(text=txt)])
      return [n.text for n in nodes]

    for x in batch_iter:
        yield x.apply(extract_and_split)

2024-09-18 02:06:39.873851: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


# Perform chunking of each field in document array for each claim

In [0]:
from mlflow.deployments import get_deploy_client


# gte-large-en Foundation models are available using the /serving-endpoints/databricks-gte-large-en/invocations api. 
deploy_client = get_deploy_client("databricks")

# NOTE: if you change your embedding model here, make sure you change it in the query step too
embeddings = deploy_client.predict(endpoint="databricks-gte-large-en", inputs={"input": ["What is Apache Spark?"]})
pprint(embeddings)

{'data': [{'embedding': [1.0458984375, -0.05426025390625, -0.28173828125, -0.0908203125,
                         0.0950927734375, -0.1337890625, 0.157470703125, 0.2822265625,
                         0.76123046875, 0.41552734375, 0.60888671875, -0.061981201171875,
                         0.10455322265625, 0.58984375, -0.400146484375, 0.35595703125, 0.5888671875,
                         0.432861328125, 0.060546875, -0.204345703125, -0.59375, 0.0997314453125,
                         -0.334716796875, -2.96875, 0.3056640625, 0.42236328125,
                         0.0021686553955078125, -0.0911865234375, -0.8515625, 0.033203125,
                         0.4892578125, 0.008209228515625, -1.4111328125, 0.418212890625,
                         0.634765625, -0.272705078125, -0.341064453125, 1.3095703125,
                         -0.280029296875, -0.7177734375, -0.2242431640625, -0.121826171875,
                         -0.76806640625, 0.09320068359375, 1.384765625, -0.01222991943359375,
  

# Compute Chunking Embeddings

In [0]:
from mlflow.exceptions import MlflowException
import logging

# Function to create embeddings using gte_large_en endpoint

In [0]:
import mlflow.deployments
deploy_client = mlflow.deployments.get_deploy_client("databricks")

@pandas_udf("array<float>")
def get_embedding(contents: pd.Series) -> pd.Series:
    
    def get_embeddings(batch):
        # NOTE: this will fail if an exception is thrown during embedding creation (add try/except if needed) 
         try:
            # Convert the batch to a list of strings
            string_batch = [str(item) for item in batch]  # Ensure all items are strings
            emb_endpoint_name = "databricks-gte-large-en"# "databricks-bge-large-en"
            response = deploy_client.predict(endpoint=emb_endpoint_name, inputs={"input": string_batch})
            return [e["embedding"] for e in response.data]
         except MlflowException as e:
            logging.error(f"Error occurred while generating embeddings: {e}")
            return [None] * len(batch)  # Return None for failed embeddings
    # splitting the contents into batches of 150 items each, since the embedding model takes at most 150 inputs per request.
    max_batch_size = 150
    batches = [contents.iloc[i:i + max_batch_size] for i in range(0, len(contents), max_batch_size)]

    # process each batch and collect the results
    all_embeddings = []
    for batch in batches:
        all_embeddings += get_embeddings(batch.tolist())

    return pd.Series(all_embeddings)

## Save Embeddings to a Delta Table

Now that the embeddings are ready, let's create a Delta table and store the embeddings in this table.

In [0]:
# %sql
# DROP TABLE IF EXISTS cmidev.cbu_ccims_poc.claim_text_embeddings

In [0]:
%sql
CREATE EXTERNAL TABLE IF NOT EXISTS cmidev.cbu_ccims_poc.claim_text_embeddings_gte (
  id BIGINT GENERATED BY DEFAULT AS IDENTITY,
  CLAIM_ID_SEQ STRING,
  DOCUMENT_CHUNK STRING,
  embedding ARRAY <FLOAT>
  -- NOTE: the table has to be CDC because VectorSearch is using DLT that is requiring CDC state
  ) 
  STORED AS PARQUET
  LOCATION '<your_path_here>'
  TBLPROPERTIES (delta.enableChangeDataFeed = true);

# Batch operation to write data from df_chunk_emd into the embeddings delta table

In [0]:
target_tbl = "cmidev.cbu_ccims_poc.claim_text_embeddings"

# define a function to append each batch of data to the Delta table  
def append_to_delta_table(batch_df, batch_id):  
    from pyspark.sql.functions import array, explode

    # Assuming df has a column named "DOCUMENT" of type STRUCT
    # and you want to create an array of some specific fields within this STRUCT
    df_transformed = batch_df.withColumn("DOCUMENT_ARRAY", array("DOCUMENT.OEM_CODE",
                                                        "DOCUMENT.DEALER",
                                                        "DOCUMENT.DISTR","DOCUMENT.FC",
                                                        "DOCUMENT.ENGINE_NAME_DESC","DOCUMENT.FAILCODE",
                                                        "DOCUMENT.SHOPORDERNUM",
                                                        "DOCUMENT.FAILURE_MODE_BUCKET",
                                                        "DOCUMENT.CLEANED_CORRECTION"))

    df_chunks = spark.createDataFrame([], schema='CLAIM_ID_SEQ INT, DOCUMENT_CHUNK STRING')

    df_chunks = (df_transformed
                    .withColumn("DOCUMENT_CHUNK", explode(df_transformed["DOCUMENT_ARRAY"]))
                    .selectExpr('CLAIM_ID_SEQ', 'DOCUMENT_CHUNK')
                )

    df_chunk_emd = (df_chunks 
                .withColumn("embedding", get_embedding("DOCUMENT_CHUNK"))
                .selectExpr("CLAIM_ID_SEQ", "DOCUMENT_CHUNK", "embedding")
                )

    df_chunk_emd.write.mode("append").option("path","abfss://cbu-ccims-poc@cmidevengineraw.dfs.core.windows.net/claim_text_embeddings")\
        .saveAsTable(target_tbl)
  
# write the PySpark DataFrame to the Delta table in batches using foreachBatch()  
df.writeStream \
    .foreachBatch(append_to_delta_table) \
    .option("checkpointLocation", "abfss://cbu-ccims-poc@cmidevengineraw.dfs.core.windows.net/checkpoint/claim_text_embeddings") \
    .trigger(Trigger.AvailableNow()) \
    .start()


## Conclusion

This notebook completed processing documents by extracting text chunks from feature table, and then by creating embeddings using a foundation model. This process included setting up an enpoint and computing embeddings for the chunks. In the final step, we stored computed embeddings in a Delta table.